# Welcome to the EMA Backtest & Plotting Notebook

### Remember, this is on a little server, so the notebook dies easily! 

But don't be alarmed. Go to Kernel > Restart & Clear Output if anything hangs. This solves all problems and can be done over and over again. I often also like Restart & Run All.

To edit fields, click in a cell and begin editing. Markdown / text fields can be edited by double clicking. Green on the left indicates editing / insert mode.

Normal / Run mode is marked by blue. You can get to it by clicking outside the cell / pressing esc. 

Run blocks of code by `Shift + Enter` (moves to next cell) or `Ctrl + Enter` (stays on current cell).

Make new cells with `Ctrl + -` or Insert > Cell Above/Below

Have fun!


In [1]:
# Imports
#from math import pi
import pandas as pd
import numpy as np
from bokeh.plotting import figure, show, output_notebook, ColumnDataSource
from bokeh.models import Range1d, LinearAxis, HoverTool
from bokeh.layouts import column
from datetime import datetime
import backtest_ema2

In [2]:
# New / temporary functions, if finished they will move to backtest_ema2
def recent_gdax(sd_str):
    engine = ms.connect_mysql()
    gdax_df = ms.get_gdax_prices(sd_str)
    return(gdax_df)

def df_resolution(trimmed_df, res_type):
    if res_type == 'day':
        df = trimmed_df.groupby(trimmed_df['time'].dt.date).agg(
    {'open':'first',  'high': max, 'low': min, 'close':'last',
     'volumeto': sum, 'volumefrom': sum,
    }).reset_index()
    elif res_type == 'minute':
        df = trimmed_df
    return(df)

# Doesn't actually combine data...
def combine_data_sources(start_time, end_time):
    #raw_data = pd.read_csv('~/backfire/data/twoseven.csv')
    #coinbase_data = pd.read_csv('~/backfire/data/coinbase_data.csv')
    raw_data = pd.read_csv('~/backfire/data/coinbase_fixed_2014-12-01_2018-05-06.csv', 
                           usecols=['time', 'open', 'low', 'high', 'close'])
    day_df, raw_data = backtest_ema2.prep_data(raw_data, start_time, end_time)
    return(day_df, raw_data)

In [35]:
# Main graphing function
def graph_candlestick(signal_df, candle_df, fills, results):
    # Prep
    buys = fills[fills['side']=='buy']
    sells = fills[fills['side']=='sell']
    inc_df = candle_df[candle_df.close > candle_df.open]
    dec_df = candle_df[candle_df.open > candle_df.close]
    if results is not None:
        my_title = f"""Final Balance: {round(results['final_bal'],2)},
        ROI: {round(results['roi'],2)}, Hodl ROI: {round(results['hodl_roi'],2)}"""
    else:
        my_title = "BTC Minute Data"
    # Width of candles... doesn't always work like it should
    #w = 18*60*60*1000 # candle period in ms
    res_len_secs = (candle_df.time[2] - candle_df.time[1]).seconds
    w = res_len_secs * 1000 # candle period in ms
    candle_tooltips = [
        ("date", "@time{%F}"),
        ("open", "@open{$0,0.00}"),
        ("low", "@low{$0,0.00}"),
        ("high", "@high{$0,0.00}"),
        ("close", "@close{$0,0.00}"),
        ]
    date_formatters={
            'time': 'datetime',
        }
    
    fill_tips = [
        ("date", "@time{%F}"),
        ("side", "@side"),
        ("btc_val", "@btc_val{0,0.000}"),
        ("usd_val", "@usd_val{$0,0.00}"),
        ]
    
    hover_tools = "crosshair,wheel_zoom,pan,box_zoom,reset,save"
    
    inc_source = ColumnDataSource(inc_df)
    dec_source = ColumnDataSource(dec_df)
    buy_source = ColumnDataSource(buys)
    sell_source = ColumnDataSource(sells)

    
    # Initialize Plot
    p = figure(
        x_axis_type = "datetime",
        tools=[hover_tools],
        toolbar_location="below",
        toolbar_sticky=False,
        active_scroll="wheel_zoom",
        plot_width = 900,
        title = my_title,
        y_range = (candle_df['close'].min()*.9, candle_df['close'].max() * 1.1),
        logo = None)
    p.grid.grid_line_alpha=0.3
    
    # Add Candles
    # Wicks
    p.segment(candle_df.time, candle_df.high,
              candle_df.time, candle_df.low,
              color="black", alpha = 0.4)
    # Bodies
    green_bar = p.vbar('time', w,
           'open', 'close',
           fill_color = "#D5E1DD", line_color = "green",
           alpha = 0.4,
          source = inc_source)
    red_bar = p.vbar('time', w,
           'open', 'close',
           fill_color = "#F2583E", line_color = "red",
           alpha = 0.4,
          source = dec_source)
    p.add_tools(HoverTool(renderers=[green_bar,red_bar], tooltips=candle_tooltips, formatters = date_formatters))
    
    # Add Buy / Sell Indicators
    buy_circle = p.circle('time', 'price', color = "green", size = 8, alpha = 0.5, source = buy_source)
    sell_circle = p.circle('time', 'price', color = "red", size = 8, alpha = 0.5, source = sell_source)
    p.add_tools(HoverTool(renderers=[buy_circle, sell_circle], tooltips=fill_tips, formatters = date_formatters))
    
    # Add Running Balance Line
    p.extra_y_ranges = {"running_bal": Range1d(start=fills.running_bal.min(), end=fills.running_bal.max())}
    p.line(fills.time, fills.running_bal, color="deepskyblue", y_range_name="running_bal", alpha = 0.8)
    p.line(fills.time, fills.p_usd, color="pink", y_range_name="running_bal", alpha = 0.2)
    p.add_layout(LinearAxis(y_range_name="running_bal"), 'right',)
    
    # Add EMA lines
    p.line(signal_df.time, signal_df.upper_ema, color="purple", alpha = 0.02)
    p.line(signal_df.time, signal_df.lower_ema, color="purple", alpha = 0.02)
    band_x = np.append(signal_df.time, signal_df.time[::-1])
    band_y = np.append(signal_df.lower_ema, signal_df.upper_ema[::-1])
    p.patch(band_x, band_y, color='purple', fill_alpha=0.03)
    return(p)



## Backtest: Load data and set variables

In [4]:
# Load Data

start_time = "2018-04-01"
end_time = "2018-05-06"

# Note, currently not actually combining data from mysql, no ram, just using csv
# Current max date 2018-05-06
day_df, minute_df = combine_data_sources(start_time, end_time)

In [5]:
# Variables

bt_vars = backtest_ema2.BacktestSettings()

upper_factor = 1 + .02
lower_factor = 1 - .02
bt_vars.set_factor_high(upper_factor)
bt_vars.set_factor_low(lower_factor)
bt_vars.set_upper_window(600)
bt_vars.set_lower_window(300)
bt_vars.set_sell_pct_btc(1)
bt_vars.set_buy_amt_usd(250)


bt_vars.set_min_usd(500)
bt_vars.set_min_btc(.001)
bt_vars.set_principle_usd(25000)
bt_vars.set_principle_btc(0)


### Note: working with Pandas DataFrames

Pandas is very easy to understand, it works like an excel spreadsheet. Some basics for you to explore the data:

View head/tail example_df.head()

View column: `example_df['my_column']`

Sum/Mean/etc column: `example_df['my_column'].max()`

View specific rows by looking up: `example_df[example_df['my_column'] == 'james']`

Pandas is very well documented so googling basic questions works very well

In [6]:
# View OLHC data
minute_df.head()

close     high      low     open                time
0  6953.00  6955.00  6928.49  6928.50 2018-04-01 00:00:00
1  6973.23  6974.93  6955.34  6955.34 2018-04-01 00:01:00
2  6992.00  6992.00  6973.23  6973.23 2018-04-01 00:02:00
3  6999.18  6999.18  6991.99  6992.00 2018-04-01 00:03:00
4  7005.00  7015.00  6999.98  6999.98 2018-04-01 00:04:00

## Backtest: Running the logic

`backtest_ema2.single_backtest` runs a single instance of a backtest and returns three pieces of information:

1. *minute_df* has columns added for signals which can be used for plotting
2. *result_overview* is a dictionary with some basic overview stats for the test. Note this is the same as a single record in the multi backtests
3. *fills_df* is a dataframe of each fill (buy / sell) made during backtest

The backtest currently is working well and can be run for any time period of data.

In [7]:
# Run backtest
minute_df, result_overview, fills_df = backtest_ema2.single_backtest(minute_df, bt_vars)

In [8]:
# View Results
pd.DataFrame([result_overview])[['sd', 'ed', 'upper_factor', 
                                 'lower_factor', 'upper_window',
                                 'lower_window', 'hodl_roi', 'roi']]

sd         ed  upper_factor  lower_factor  upper_window  \
0 2018-04-01 2018-05-06          1.02          0.98           600   

   lower_window  hodl_roi       roi  
0           300  0.409464  0.019434

## Backtest: Plotting results with Bokeh

`graph_candlestick()` is the only graphing function currently. It builds a plot called p which is then displayed with `show(p)`


* We can't graph more than a few days of minute_df it doesn't display well and can also cause the notebook to stall
* To plot longer periods of time use day_df ie, `candle_df = day_df`
    * Note TODO: graphing day_df is still slow, probably from the ema lines being minute data still
* Bokeh is fairly straight forward, feel free to play with the graph above to add lines you'd like


In [36]:
# TODO: combine data and only pass one df
# TODO: minute vs day data

p = graph_candlestick(signal_df = minute_df, 
                      candle_df = minute_df, 
                      fills = fills_df,
                      results = result_overview)
output_notebook()
show(p)

Loading BokehJS ...

In [10]:
fills_df

btc_val    price  side                time      usd_val  p_usd  p_btc  \
0    0.036915  6765.55   buy 2018-04-01 07:23:00  -250.000000  25000      0   
1    0.036923  6764.01   buy 2018-04-01 07:30:00  -250.000000  25000      0   
2    0.037171  6719.00   buy 2018-04-01 08:16:00  -250.000000  25000      0   
3    0.037388  6680.00   buy 2018-04-01 09:03:00  -250.000000  25000      0   
4    0.037491  6661.60   buy 2018-04-01 09:17:00  -250.000000  25000      0   
5    0.038025  6568.00   buy 2018-04-01 13:29:00  -250.000000  25000      0   
6    0.038095  6556.01   buy 2018-04-01 14:00:00  -250.000000  25000      0   
7    0.038347  6512.97   buy 2018-04-01 14:42:00  -250.000000  25000      0   
8    0.038364  6510.00   buy 2018-04-01 14:45:00  -250.000000  25000      0   
9    0.038476  6490.99   buy 2018-04-01 14:49:00  -250.000000  25000      0   
10   0.038376  6507.96   buy 2018-04-01 14:51:00  -250.000000  25000      0   
11   0.038423  6500.01   buy 2018-04-01 14:56:00  -250.000000  25000      0   
12   0.038631  6465.01   buy 2018-04-01 15:44:00  -250.000000  25000      0   
13   0.038660  6460.17   buy 2018-04-01 15:56:00  -250.000000  25000      0   
14   0.038721  6450.01   buy 2018-04-01 15:59:00  -250.000000  25000      0   
15  -0.570006  6848.02  sell 2018-04-01 16:32:00  3899.507989  25000      0   
16   0.034930  7150.00   buy 2018-04-04 09:19:00  -250.000000  25000      0   
17   0.035221  7091.01   buy 2018-04-04 10:32:00  -250.000000  25000      0   
18   0.035360  7063.03   buy 2018-04-04 11:01:00  -250.000000  25000      0   
19   0.035426  7050.00   buy 2018-04-04 11:08:00  -250.000000  25000      0   
20   0.035381  7058.79   buy 2018-04-04 11:14:00  -250.000000  25000      0   
21   0.035506  7034.00   buy 2018-04-04 11:32:00  -250.000000  25000      0   
22   0.035935  6950.00   buy 2018-04-04 14:04:00  -250.000000  25000      0   
23   0.036290  6882.01   buy 2018-04-04 15:10:00  -250.000000  25000      0   
24   0.036385  6864.01   buy 2018-04-04 15:14:00  -250.000000  25000      0   
25   0.036593  6825.00   buy 2018-04-04 15:55:00  -250.000000  25000      0   
26   0.036609  6822.04   buy 2018-04-04 16:07:00  -250.000000  25000      0   
27   0.036588  6826.01   buy 2018-04-04 16:17:00  -250.000000  25000      0   
28   0.036988  6752.25   buy 2018-04-04 18:13:00  -250.000000  25000      0   
29   0.037687  6627.00   buy 2018-04-05 01:26:00  -250.000000  25000      0   
..        ...      ...   ...                 ...          ...    ...    ...   
75   0.028046  8905.00   buy 2018-04-25 14:12:00  -250.000000  25000      0   
76   0.027917  8946.02   buy 2018-04-25 14:17:00  -250.000000  25000      0   
77   0.028252  8840.01   buy 2018-04-25 15:16:00  -250.000000  25000      0   
78   0.028313  8821.00   buy 2018-04-25 15:38:00  -250.000000  25000      0   
79   0.028426  8786.00   buy 2018-04-25 16:27:00  -250.000000  25000      0   
80   0.028302  8824.46   buy 2018-04-25 23:28:00  -250.000000  25000      0   
81   0.028246  8842.00   buy 2018-04-25 23:38:00  -250.000000  25000      0   
82   0.028260  8837.49   buy 2018-04-25 23:40:00  -250.000000  25000      0   
83   0.028390  8796.99   buy 2018-04-25 23:43:00  -250.000000  25000      0   
84   0.028308  8822.60   buy 2018-04-25 23:50:00  -250.000000  25000      0   
85   0.028438  8782.41   buy 2018-04-26 00:04:00  -250.000000  25000      0   
86   0.028429  8785.00   buy 2018-04-26 00:19:00  -250.000000  25000      0   
87   0.028555  8746.13   buy 2018-04-26 00:44:00  -250.000000  25000      0   
88   0.028541  8750.61   buy 2018-04-26 00:47:00  -250.000000  25000      0   
89  -0.778149  9050.53  sell 2018-04-26 20:10:00  7035.618437  25000      0   
90   0.027716  9011.00   buy 2018-04-27 20:36:00  -250.000000  25000      0   
91   0.027705  9014.51   buy 2018-04-27 20:38:00  -250.000000  25000      0   
92   0.027793  8986.14   buy 2018-04-27 20:48:00  -250.000000  25000      0   
93   0.027789  8987.28   buy 2018-04-27 20:55:00  -250.0